# Expected Value of Cost function in population setting
## Projecting $p$ entries as sigmoids 
We have 

$$C(A, P) = \text{Tr}\left((B^* - B)\Sigma_X(B^* - B)\right),$$

where $$B = P^{-1}AP.$$

Here, $A$ is lower triangular and $P$ is a doubly stochastic matrix, namely

\begin{align*}
0 \leq &p_{ij} &\forall\ i,j = 1, \cdots, n\\
\sum_{j = 1}^n &p_{ij} = 1&\forall\ i = 1, \cdots, n\\
\sum_{i=1}^n &p_{ij} = 1 &\forall\ j = 1, \cdots, n\\
\end{align*}

## Dealing with the constraints
### Non-negativity constraints
To deal with the constraints that $p$ must be non-negative, we project the entries by applying the sigmoid function of each entry. Note that the range of the sigmoid is $(0, 1)$, which is also what we require for our entries $p$ (we did not explicitly constrain $p$ to be smaller than 1, but the equality constraints combined with the non-negativity constraints make sure that is the case.

Hence, 

$$P = \sigma(P_{\sigma}),$$

where $\sigma(\cdot)$ indicates the element-wise application of the sigmoid function 

$$\sigma(x) = \frac{1}{1 + e^{-x}}.$$

So, instead of directly estimating $P$, we estimate $P_\sigma$. The constraints now becomes an equality constrained program

\begin{align*}
\sum_{j = 1}^n &p_{ij} = 1&\forall\ i = 1, \cdots, n\\
\sum_{i=1}^n &p_{ij} = 1 &\forall\ j = 1, \cdots, n\\
\end{align*}

## Dealing with equality constraints
To deal with the $2n$ equality constraints, we use $\textit{lagrange multipliers}$ $\lambda_{row, i}$, $i = 1, \cdots, n$ and $\lambda_{col, j}$, $j = 1, \cdots, n$. The dual function now becomes 

$$\mathcal{L}(A, P_\sigma, \mathbf{\lambda}) = C(A, P) - \sum_{i=1}^n \lambda_{row, i} \left(\sum_{j = 1}^n p_{ij} - 1\right) - \sum_{j = 1}^n \lambda_{col, j} \left(\sum_{i = 1}^n p_{ij} - 1\right),$$
where $P = \sigma(P_\sigma)$

## Optimizing $\mathcal{L}(A, P_\sigma, \mathbf{\lambda})$
let $$q(\mathbf{\lambda}) = \inf_{A, P_{sigma}} \mathcal{L}(A, P_\sigma, \mathbf{\lambda}).$$
Then the $\textit{dual problem}$ is $$\max_{\mathbf{\lambda}} q(\mathbf{\lambda}).$$

## Deriving $q(\mathbf{\lambda})$
To minimize $\mathcal{L}(A, P_\sigma, \mathbf{\lambda})$, we will use gradient descent.

The partial derivative with respect to entries in $A$ is simple, 

$$\frac{\partial\mathcal{L}(A, P_\sigma, \mathbf{\lambda})}{\partial a_{ij}} = \frac{\partial C(A, P)}{\partial a_{ij}}$$

Now, the partial derivative with respect to the entries in $p$ is more involved as it occurs also in exactly two equality constraints, namely in $\lambda_{row, i}$ and in $\lambda{col, j}$.

$$\frac{\partial\mathcal{L}(A, P_\sigma, \mathbf{\lambda})}{\partial p_{ij}} = \frac{\partial C(A, P)}{\partial p_{ij}} - \lambda_{row, i}p_{ij} - \lambda_{col, j}p_{ij}.$$

Now, as $C(A, P)$ is unfortunately yet inevitably non-convex, we cannot expect to find the infimum $q(\mathbf{\lambda})$. However, let us consider a local minimum $\tilde{q}(\mathbf{\lambda})$, which we will find by gradient descent. Let us start with an initial matrix $A_0$ (e.g. the non-zero matrix) and an initial unconstrained matrix $P_{0,\sigma} = Z$, where $Z \sim \mathcal{N}(\mathbf{0}, I_{n^2})$. So, $P_\sigma$ is close to zero, but there is some perturbation to make sure the matrix is non-singular.

For a sufficiently small step size, we will do this gradient descent until we have found a stationary point:
$$(A_{t + 1}, P_{t + 1}) = (A_t, P_t) - \eta\ \nabla \mathcal{L}(A_t, P_t, \mathbf{\lambda})$$
Note that this is an $\textit{unconstrained}$ optimization problem now, which should make things more easy. 

Suppose that after a number of iterations, we have found this local minimum with parameters $\tilde{A}$, $\tilde{P}$. Then, we have that $$\tilde{q}(\mathbf{\lambda}) = \mathcal{L}(\tilde{A}, \tilde{P}, \mathbf{\lambda}).$$

## Deriving the dual problem
Now that we have $\tilde{q}(\mathbf{\lambda})$, the solution to the dual problem is
$$\max_{\lambda} \tilde{q}(\mathbf{\lambda}),$$
which is again an unconstrained optimization problem, which we can also optimize by maximizing $\lambda$'s.

In [2]:
import numpy as np

In [3]:
# actual solution
n = 3
As = np.tril(np.random.rand(n, n))
Ps = np.identity(n)
Sigma = np.identity(n)

print(f"A*:\n{np.round(As, 2)}\n\nP*:\n{Ps}")

A*:
[[0.93 0.   0.  ]
 [0.85 0.98 0.  ]
 [0.72 0.85 0.06]]

P*:
[[1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]]


In [4]:
def expected_cost(A, P, As = As, Ps = Ps):
    # base on the distribution of X, no actual data needed.
    # we need the covariance of X_t - X_{t-1}.
    # Then, the expected cost is the trace of this covariance
    P_inv = np.linalg.inv(P)
    Ps_inv = np.linalg.inv(Ps)
    
    B = np.matmul(P_inv, np.matmul(A, P))
    Bs = np.matmul(Ps_inv, np.matmul(As, Ps))
    
    covariance_X = np.matmul(np.linalg.inv(np.identity(n ** 2) - np.kron(Bs, Bs)), Sigma.reshape(n ** 2)).reshape((n, n))
    
    covariance_matrix = Sigma + np.matmul((Bs - B), np.matmul(covariance_X, (Bs - B).transpose()))
    
    return np.trace(covariance_matrix)

In [5]:
print(f"Expected cost: {expected_cost(np.random.rand(n,n), Ps)}.")

Expected cost: 5592.98383841046.


In [70]:
def sigmoid(x):
    return 1 / (1 + np.exp(-x))

# get gradient of our outcome
def grad_a(A, Psigma, i, j, As = As, Ps = Ps):
    P = sigmoid(Psigma)
    P_inv = np.linalg.inv(P)
    Ps_inv = np.linalg.inv(Ps)
    
    B = np.matmul(P_inv, np.matmul(A, P))
    Bs = np.matmul(Ps_inv, np.matmul(As, Ps))
    
    J = np.zeros((n, n))
    J[i][j] = 1
    
    covariance_X = np.matmul(np.linalg.inv(np.identity(n ** 2) - np.kron(Bs, Bs)), Sigma.reshape(n ** 2)).reshape((n, n))

    return -2 * np.trace(np.matmul(covariance_X, np.matmul((Bs - B).transpose(), np.matmul(P_inv, np.matmul(J, P)))))

def grad_p(A, Psigma, i, j, As = As, Ps = Ps):
    P = sigmoid(Psigma)
    P_inv = np.linalg.inv(P)
    Ps_inv = np.linalg.inv(Ps)
    
    B = np.matmul(P_inv, np.matmul(A, P))
    Bs = np.matmul(Ps_inv, np.matmul(As, Ps))
    
    J = np.zeros((n, n))
    J[i][j] = 1
    
    covariance_X = np.matmul(np.linalg.inv(np.identity(n ** 2) - np.kron(Bs, Bs)), Sigma.reshape(n ** 2)).reshape((n, n))

    B_grad = np.matmul(P_inv, np.matmul(A, J))
    B_grad -= np.matmul(P_inv, np.matmul(J, np.matmul(P_inv, np.matmul(A, P))))
    
    return -2 * np.trace(np.matmul(covariance_X, np.matmul((Bs - B).transpose(), B_grad))) #* sigmoid(P[i][j]) * (1 - sigmoid(P[i][j]))

def get_gradient(A, P):
    gradient = np.zeros(int(n * (n + 1) / 2 + n ** 2))
    index = 0
    
    for i in range(n):
        for j in range(i + 1):
            gradient[index] = grad_a(A, P, i, j)
            index += 1
            
    for i in range(n):
        for j in range(n):
            gradient[index] = grad_p(A, P, i, j)
            index += 1
    return gradient

0.19661193324148185
[[ 0.          0.09685158  0.        ]
 [-0.29737716  0.         -0.85045194]
 [ 0.          0.40104964  0.        ]]
-271.2496227567504


In [81]:
A = np.zeros((n, n))
P = np.ones((n, n)) / n + np.random.rand(n, n) / n
print(P)
eta = 1e-9

[[0.45786214 0.37112916 0.40963184]
 [0.61518258 0.54761015 0.44460922]
 [0.43560532 0.59531367 0.61896613]]


In [ ]:
grad = get_gradient(A, P)
print(np.sum(grad))
while np.sum(np.abs(grad)) > 10:
    A_grad = np.zeros((n , n))
    A_grad[np.tril_indices(n)] = grad[:int(n * (n + 1) / 2)]
    P_grad = grad[int(n * (n + 1) / 2):].reshape((n , n))

    A -= eta * A_grad * 10
    P -= eta * P_grad
    
    grad = get_gradient(A, P)
    
    print(P)
    print(expected_cost(A, P))    
    
# P = sinkhorn_balance(P)

# print(A_grad)
# print(P_grad)
#print(A, P)
#print(expected_cost(A, P))

-45529.57321312775
[[0.45786214 0.37112916 0.40963184]
 [0.61518258 0.54761015 0.44460922]
 [0.43560532 0.59531367 0.61896613]]
4721.725950155766
[[0.45786093 0.37113068 0.40963161]
 [0.61518256 0.5476102  0.44460923]
 [0.43560658 0.59531216 0.6189664 ]]
4707.371633780372
[[0.45785868 0.37113347 0.4096312 ]
 [0.61518243 0.54761038 0.44460923]
 [0.435609   0.59530924 0.61896693]]
4693.17815390949
[[0.45785557 0.37113733 0.40963064]
 [0.61518211 0.54761082 0.44460921]
 [0.43561251 0.59530502 0.61896769]]
4679.141903954818
[[0.45785177 0.37114204 0.40962997]
 [0.61518152 0.5476116  0.44460915]
 [0.43561702 0.59529961 0.61896864]]
4665.25954513039
[[0.45784745 0.37114738 0.40962922]
 [0.61518058 0.54761282 0.44460903]
 [0.43562246 0.5952931  0.61896978]]
4651.52798400497
[[0.45784277 0.37115317 0.40962842]
 [0.61517921 0.54761456 0.44460884]
 [0.43562875 0.59528559 0.61897108]]
4637.94435185539
[[0.45783788 0.37115919 0.40962761]
 [0.61517733 0.54761692 0.44460858]
 [0.43563581 0.59527719 

 [0.43537109 0.59551327 0.61899789]]
4030.1234023910183
[[0.46103991 0.36775209 0.40971077]
 [0.6125861  0.55038285 0.4444794 ]
 [0.43533428 0.59554916 0.61899836]]
4023.0618988322212
[[0.46117375 0.36761832 0.40970505]
 [0.61250112 0.55046634 0.44448174]
 [0.43529614 0.59558618 0.618999  ]]
4016.073004144906
[[0.46130993 0.36748278 0.40969864]
 [0.61241531 0.5505503  0.44448446]
 [0.43525668 0.59562432 0.61899983]]
4009.155864066097
[[0.46144838 0.36734555 0.40969154]
 [0.61232868 0.55063466 0.44448756]
 [0.4352159  0.59566356 0.61900086]]
4002.3096393515725
[[0.46158908 0.36720668 0.40968372]
 [0.6122413  0.5507194  0.44449105]
 [0.4351738  0.5957039  0.6190021 ]]
3995.5335057520215
[[0.46173197 0.36706623 0.40967517]
 [0.61215319 0.55080445 0.44449492]
 [0.43513038 0.59574532 0.61900356]]
3988.8266539457104
[[0.46187701 0.36692427 0.40966587]
 [0.61206439 0.55088978 0.44449919]
 [0.43508565 0.5957878  0.61900526]]
3982.1882894311475
[[0.46202415 0.36678085 0.40965582]
 [0.61197494 0

 [0.42904349 0.60063036 0.62013119]]
3652.006045094202
[[0.47525498 0.35564032 0.40691297]
 [0.60591804 0.55597564 0.44553524]
 [0.42892107 0.60071746 0.62016503]]
3648.8068041417705
[[0.47546168 0.35548639 0.40684862]
 [0.60585171 0.55602207 0.44555318]
 [0.42879779 0.60080489 0.6201994 ]]
3645.640710124493
[[0.47566843 0.35533289 0.40678376]
 [0.60578622 0.55606773 0.445571  ]
 [0.42867366 0.60089263 0.62023429]]
3642.5074093003786
[[0.47587523 0.3551798  0.40671839]
 [0.60572156 0.55611261 0.44558871]
 [0.42854868 0.60098069 0.6202697 ]]
3639.4065499639473
[[0.47608206 0.35502713 0.40665252]
 [0.60565773 0.55615673 0.4456063 ]
 [0.42842286 0.60106905 0.62030564]]
3636.3377824539334
[[0.47628891 0.35487488 0.40658616]
 [0.60559475 0.55620009 0.44562376]
 [0.4282962  0.60115772 0.6203421 ]]
3633.3007591625037
[[0.47649577 0.35472305 0.40651932]
 [0.6055326  0.55624269 0.44564108]
 [0.42816872 0.60124669 0.62037908]]
3630.2951345458496
[[0.47670264 0.35457165 0.40645201]
 [0.6054713  0

 [0.41860325 0.6073819  0.62369422]]
3489.1761124250397
[[0.48970944 0.34569824 0.40147834]
 [0.60320527 0.55764553 0.44631123]
 [0.41843672 0.60748243 0.62375822]]
3487.5813355474857
[[0.48990731 0.34557031 0.40139416]
 [0.60319236 0.55765055 0.44631367]
 [0.41826981 0.60758305 0.6238225 ]]
3486.0004115017123
[[0.490105   0.34544263 0.40130987]
 [0.60318    0.55765521 0.44631587]
 [0.41810253 0.60768375 0.62388706]]
3484.4331586564667
[[0.49030252 0.3453152  0.40122547]
 [0.60316819 0.55765951 0.44631786]
 [0.41793488 0.60778454 0.6239519 ]]
3482.8793977556916
[[0.49049986 0.34518801 0.40114097]
 [0.60315691 0.55766345 0.44631962]
 [0.41776688 0.60788541 0.62401701]]
3481.338951901198
[[0.49069703 0.34506107 0.40105637]
 [0.60314616 0.55766704 0.44632117]
 [0.41759852 0.60798636 0.62408239]]
3479.811646534912
[[0.49089403 0.34493437 0.40097167]
 [0.60313594 0.55767029 0.4463225 ]
 [0.41742981 0.60808739 0.62414803]]
3478.297309420702
[[0.49109086 0.34480791 0.40088688]
 [0.60312623 0.

 [0.40562175 0.61495355 0.62894711]]
3399.212183314352
[[0.50395072 0.33671528 0.39508897]
 [0.60330138 0.55733891 0.44603235]
 [0.40544167 0.61505644 0.6290221 ]]
3398.2823450281317
[[0.50413874 0.33659822 0.39500173]
 [0.60331164 0.55732908 0.44602441]
 [0.40526157 0.61515933 0.62909713]]
3397.357994180342
[[0.50432667 0.33648123 0.39491449]
 [0.60332201 0.55731919 0.44601642]
 [0.40508145 0.6152622  0.62917219]]
3396.4390690625783
[[0.50451451 0.33636429 0.39482725]
 [0.60333249 0.55730922 0.44600838]
 [0.40490132 0.61536505 0.62924727]]
3395.525508871713
[[0.50470227 0.33624742 0.39474001]
 [0.60334306 0.5572992  0.44600029]
 [0.40472118 0.61546789 0.62932239]]
3394.6172536953372
[[0.50488994 0.33613061 0.39465278]
 [0.60335373 0.55728911 0.44599215]
 [0.40454103 0.61557071 0.62939753]]
3393.714244497402
[[0.50507752 0.33601385 0.39456555]
 [0.60336449 0.55727896 0.44598396]
 [0.40436087 0.61567351 0.62947269]]
3392.81642310408
[[0.50526502 0.33589715 0.39447832]
 [0.60337534 0.557

...

[[ 1.67131401 -0.88345105 -0.34922347]
 [ 0.31424389  0.61577009  0.32647956]
 [-0.22186098  1.11554832  0.95718125]]
432.8702340964259
[[ 1.67131445 -0.883452   -0.34922443]
 [ 0.31425372  0.61576018  0.32646865]
 [-0.22186994  1.11555553  0.95718949]]
432.8578151004003
[[ 1.67131489 -0.88345295 -0.34922539]
 [ 0.31426356  0.61575027  0.32645774]
 [-0.2218789   1.11556273  0.95719773]]
432.8453963363203
[[ 1.67131533 -0.88345391 -0.34922634]
 [ 0.31427339  0.61574037  0.32644683]
 [-0.22188786  1.11556993  0.95720597]]
432.8329778042034
[[ 1.67131577 -0.88345486 -0.3492273 ]
 [ 0.31428322  0.61573046  0.32643591]
 [-0.22189682  1.11557713  0.95721421]]
432.8205595040704
[[ 1.67131621 -0.88345581 -0.34922826]
 [ 0.31429305  0.61572055  0.326425  ]
 [-0.22190577  1.11558433  0.95722245]]
432.8081414359377
[[ 1.67131665 -0.88345676 -0.34922921]
 [ 0.31430289  0.61571064  0.32641409]
 [-0.22191473  1.11559153  0.95723069]]
432.7957235998261
[[ 1.67131708 -0.88345771 -0.34923017]
 [ 0.3143

 [-0.22245226  1.11602332  0.95772543]]
432.05107873604874
[[ 1.67134289 -0.88351422 -0.34928689]
 [ 0.31490316  0.61510615  0.32574762]
 [-0.22246122  1.11603052  0.95773368]]
432.0386750884251
[[ 1.67134332 -0.88351515 -0.34928782]
 [ 0.31491301  0.61509624  0.32573668]
 [-0.22247018  1.11603771  0.95774193]]
432.02627167397554
[[ 1.67134374 -0.88351609 -0.34928876]
 [ 0.31492286  0.61508633  0.32572574]
 [-0.22247914  1.1160449   0.95775018]]
432.0138684927168
[[ 1.67134416 -0.88351702 -0.34928969]
 [ 0.31493271  0.61507642  0.3257148 ]
 [-0.2224881   1.11605209  0.95775843]]
432.0014655446689
[[ 1.67134458 -0.88351795 -0.34929063]
 [ 0.31494255  0.61506651  0.32570386]
 [-0.22249706  1.11605929  0.95776669]]
431.98906282984905
[[ 1.671345   -0.88351888 -0.34929156]
 [ 0.3149524   0.61505659  0.32569292]
 [-0.22250601  1.11606648  0.95777494]]
431.97666034827716
[[ 1.67134542 -0.88351981 -0.3492925 ]
 [ 0.31496225  0.61504668  0.32568198]
 [-0.22251497  1.11607367  0.95778319]]
431.

 [-0.22308834  1.11653376  0.95831171]]
431.1710002415948
[[ 1.6713721  -0.88357961 -0.34935247]
 [ 0.31560298  0.61440223  0.32496991]
 [-0.2230973   1.11654094  0.95831997]]
431.15861319491336
[[ 1.6713725  -0.88358052 -0.34935338]
 [ 0.31561285  0.61439231  0.32495894]
 [-0.22310626  1.11654813  0.95832824]]
431.14622638270487
[[ 1.6713729  -0.88358143 -0.34935429]
 [ 0.31562271  0.61438239  0.32494797]
 [-0.22311522  1.11655531  0.9583365 ]]
431.1338398049881
[[ 1.6713733  -0.88358234 -0.3493552 ]
 [ 0.31563258  0.61437248  0.324937  ]
 [-0.22312418  1.1165625   0.95834477]]
431.1214534617807
[[ 1.67137371 -0.88358325 -0.34935611]
 [ 0.31564245  0.61436256  0.32492603]
 [-0.22313314  1.11656968  0.95835303]]
431.10906735310243
[[ 1.67137411 -0.88358415 -0.34935703]
 [ 0.31565231  0.61435264  0.32491506]
 [-0.2231421   1.11657687  0.9583613 ]]
431.0966814789691
[[ 1.6713745  -0.88358506 -0.34935794]
 [ 0.31566218  0.61434272  0.32490409]
 [-0.22315106  1.11658405  0.95836956]]
431.0

 [-0.22374235  1.11705798  0.95891545]]
430.26736315486113
[[ 1.67140063 -0.88364518 -0.34941816]
 [ 0.31632379  0.6136781   0.32416806]
 [-0.22375131  1.11706515  0.95892373]]
430.25499327219774
[[ 1.67140101 -0.88364606 -0.34941905]
 [ 0.31633368  0.61366818  0.32415706]
 [-0.22376027  1.11707233  0.958932  ]]
430.24262362532085
[[ 1.67140139 -0.88364695 -0.34941993]
 [ 0.31634356  0.61365826  0.32414606]
 [-0.22376922  1.11707951  0.95894028]]
430.23025421425086
[[ 1.67140177 -0.88364784 -0.34942082]
 [ 0.31635344  0.61364834  0.32413506]
 [-0.22377818  1.11708668  0.95894856]]
430.2178850390038
[[ 1.67140215 -0.88364872 -0.34942171]
 [ 0.31636333  0.61363841  0.32412406]
 [-0.22378714  1.11709386  0.95895684]]
430.20551609959807
[[ 1.67140253 -0.88364961 -0.34942259]
 [ 0.31637321  0.61362849  0.32411306]
 [-0.2237961   1.11710104  0.95896512]]
430.1931473960509
[[ 1.67140291 -0.88365049 -0.34942348]
 [ 0.31638309  0.61361857  0.32410205]
 [-0.22380506  1.11710821  0.95897339]]
430

 [-0.2242978   1.11750272  0.95942897]]
429.50087697691555
[[ 1.67142367 -0.88369954 -0.34947256]
 [ 0.31693699  0.6130628   0.32348527]
 [-0.22430676  1.11750989  0.95943725]]
429.4885217466785
[[ 1.67142403 -0.88370041 -0.34947343]
 [ 0.31694689  0.61305288  0.32347424]
 [-0.22431572  1.11751706  0.95944554]]
429.47616675332773
[[ 1.67142439 -0.88370128 -0.3494743 ]
 [ 0.31695679  0.61304295  0.32346322]
 [-0.22432468  1.11752423  0.95945383]]
429.4638119968801
[[ 1.67142475 -0.88370214 -0.34947517]
 [ 0.31696669  0.61303303  0.32345219]
 [-0.22433364  1.1175314   0.95946212]]
429.4514574773537
[[ 1.67142512 -0.88370301 -0.34947603]
 [ 0.31697659  0.6130231   0.32344116]
 [-0.2243426   1.11753857  0.95947041]]
429.43910319476703
[[ 1.67142548 -0.88370388 -0.3494769 ]
 [ 0.31698649  0.61301317  0.32343013]
 [-0.22435156  1.11754574  0.9594787 ]]
429.42674914913636
[[ 1.67142584 -0.88370474 -0.34947776]
 [ 0.31699639  0.61300325  0.32341911]
 [-0.22436052  1.11755291  0.95948699]]
429.

In [44]:
print(A,P)

[[ 0.99898515  0.          0.        ]
 [ 0.63514367  0.33752585  0.        ]
 [ 0.04119225 -0.034471    0.53300707]] [[ 0.25527284  0.98999339 -0.0759014 ]
 [ 0.01340492 -0.02065715  0.98185955]
 [ 0.99973441 -0.0047746  -0.0029553 ]]


In [5791]:
def sinkhorn_balance(P):
    for _ in range(10000):
        # normalize rows
        r_sum = P.sum(axis=1)
        P = P / r_sum[:, np.newaxis]
        
        
        c_sum = P.sum(axis = 0)
        P = P / c_sum
    return P

Ps = np.array([[0.4, 0.1, 0.5], [0.1, 0.4, 0.6], [1, 2, 4]])
print(sinkhorn_balance(Ps))

[[0.59965663 0.1187942  0.28154917]
 [0.15568219 0.4934595  0.35085831]
 [0.24466118 0.3877463  0.36759252]]
